# JavaScripty with Numbers and Function - without Dynamaic Typing

In [1]:
trait Expr                                       // e
case class N(n: Double) extends Expr             // e ::= n
case class Fun(x: String, e1: Expr) extends Expr // e ::= (x) => e1
case class Var(x: String) extends Expr           // e ::= x
case class Call(e1: Expr, e2: Expr) extends Expr // e ::= e1(e2)

def isValue(e: Expr): Boolean = e match {
  case N(_) | Fun(_, _) => true
  case _ => false
}

defined trait Expr
defined class N
defined class Fun
defined class Var
defined class Call
defined function isValue

In [67]:
def subst(v: Expr, x: String, e: Expr) = {
  def subst(e: Expr): Expr = e match {
    case N(_) => e
    case Fun(y, e1) => if (x == y) e else Fun(y, subst(e1))
    case Var(y) => if (x == y) v else e
    case Call(e1, e2) => Call(subst(e1), subst(e2))
  }
  subst(e)
}

def step(e: Expr): Expr = e match {
  // DoCall
  case Call(Fun(x, e1), v2) if isValue(v2) => subst(v2, x, e1)
  // SearchCall2
  case Call(v1, e2) if isValue(v1) => Call(v1, step(e2))
  // SearchCall1
  case Call(e1, e2) => Call(step(e1), e2)
}

defined function subst
defined function step

## Positive Test

In [68]:
step(Call(Fun("x", Var("x")), N(4)))

res68: Expr = N(n = 4.0)

## What happens here? 

In [69]:
step(Call(N(4), N(2)))

scala.MatchError: N(2.0) (of class ammonite.$sess.cmd66$Helper$N)

# With Dynamic Typing

In [70]:
case class DynamicTypeError(e: Expr)

defined class DynamicTypeError

In [71]:
def step(e: Expr): Either[DynamicTypeError, Expr] = e match {
  case Call(v1, v2) if isValue(v1) && isValue(v2) => v1 match {
    // DoCall
    case Fun(x, e1) => Right( subst(v2, x, e1) )
    // TypeErrorCall
    case _ => Left( DynamicTypeError(e) )
  }
  // SearchCall2 and PropagateCall2
  case Call(v1, e2) if isValue(v1) => step(e2) map { e2 => Call(v1, e2) }
  // SearchCall1 and PropagateCall1
  case Call(e1, e2) => step(e1) match {
    case l @ Left(_) => l
    case Right(e1_) => Right(Call(e1_, e2))
  }
}

defined function step

## Tests

In [72]:
// 5(3)
val ill_typed = Call(N(5), N(3))
step(ill_typed)
val ill_typed1 = Call(Var("5"),N(3))
step(ill_typed1)
// indicates something wrong with our impelementation, we need to allow for binding variables with const and handle open expressions appropiately

scala.MatchError: Var(5) (of class ammonite.$sess.cmd66$Helper$Var)

# Static Typing

In [73]:
trait Typ                                                 // τ
case object TNumber extends Typ                           // τ ::= number
case class TFun(xt: (String, Typ), tret: Typ) extends Typ // τ ::= (x: τ) => τ'

trait Expr                                               // e
case class N(n: Double) extends Expr                     // e ::= n
case class Fun(xt: (String, Typ), e1: Expr) extends Expr // e ::= (x: τ) => e1
case class Var(x: String) extends Expr                   // e ::= x
case class Call(e1: Expr, e2: Expr) extends Expr         // e ::= e1(e2)

def isValue(e: Expr): Boolean = e match {
  case N(_) | Fun(_, _) => true
  case _ => false
}

defined trait Typ
defined object TNumber
defined class TFun
defined trait Expr
defined class N
defined class Fun
defined class Var
defined class Call
defined function isValue

In [74]:
type TEnv = Map[String, Typ] // Γ


defined type TEnv

In [75]:
def hastype(e: Expr): Typ = {
  def hastype(tenv: TEnv, e: Expr): Typ = e match {
    // TypeNumber
    case N(_) => TNumber
    // TypeFunction
    case Fun((x,t), e1) => TFun((x,t), hastype(tenv + (x -> t), e1))
    // TypeVar
    case Var(x) => tenv(x)
    // TypeCall
    case Call(e1, e2) => hastype(tenv, e1) match {
      case TFun((_,t), tret) if t == hastype(tenv, e2) => tret
    }
  }
  hastype(Map.empty, e)
}

defined function hastype

## Tests

In [76]:
val e_welltyped = Call(Fun(("i", TNumber), Var("i")), N(4))
val e_illtyped = Call(N(3), N(4)) 

e_welltyped: Call = Call(
  e1 = Fun(xt = ("i", TNumber), e1 = Var(x = "i")),
  e2 = N(n = 4.0)
)
e_illtyped: Call = Call(e1 = N(n = 3.0), e2 = N(n = 4.0))

In [77]:
hastype(e_welltyped)

res77: Typ = TNumber

In [78]:
hastype(e_illtyped)

scala.MatchError: TNumber (of class ammonite.$sess.cmd73$Helper$TNumber$)

# Fix for better error message

In [79]:
case class StaticTypeError(tbad: Typ, esub: Expr, e: Expr) extends Exception {
  override def toString: String = s"invalid type ${tbad} for sub-expression ${esub} in ${e}"
}

def hastype(e: Expr): Typ = {
  def hastype(tenv: TEnv, e: Expr): Typ = e match {
    // TypeNumber
    case N(_) => TNumber
    // TypeFunction
    case Fun((x,t), e1) => TFun((x,t), hastype(tenv + (x -> t), e1))
    // TypeVar
    case Var(x) => tenv(x)
    // TypeCall
    case Call(e1, e2) => hastype(tenv, e1) match {
      case TFun((_,t), tret) if t == hastype(tenv, e2) => tret
      case tbad => throw StaticTypeError(tbad, e1, e)
    }
  }
  hastype(Map.empty, e)
}

defined class StaticTypeError
defined function hastype

## Tests

In [80]:
hastype(e_illtyped)

ammonite.$sess.cmd79$Helper$StaticTypeError: null

In [81]:
// val e_illtyped = Call(Fun(("i", TNumber), Var("y")), N(4))
hastype(e_welltyped)


res81: Typ = TNumber

# Putting it all together

## add step

In [82]:
def subst(v: Expr, x: String, e: Expr) = {
  def subst(e: Expr): Expr = e match {
    case N(_) => e
    case Fun(yt @ (y, _), e1) => if (x == y) e else Fun(yt, subst(e1))
    case Var(y) => if (x == y) v else e
    case Call(e1, e2) => Call(subst(e1), subst(e2))
  }
  subst(e)
}

def step(e: Expr): Expr = {
  require(!isValue(e))
  e match {
    // DoCall
    case Call(Fun((y, _), e1), v2) => subst(v2, y, e1)
    // SearchCall2
    case Call(v1, e2) if isValue(v1) => Call(v1, step(e2))
    // SearchCall1
    case Call(e1, e2) => Call(step(e1), e2)
  }
}

defined function subst
defined function step

## Tests

In [83]:
val e_welltyped = Call(Fun(("i", TNumber), Var("i")), N(4))
hastype(e_welltyped)
step(e_welltyped)

e_welltyped: Call = Call(
  e1 = Fun(xt = ("i", TNumber), e1 = Var(x = "i")),
  e2 = N(n = 4.0)
)
res83_1: Typ = TNumber
res83_2: Expr = N(n = 4.0)

## Add iterate step

In [84]:
def iterate[A](acc: A)(step: A => Option[A]): A = {
  def loop(acc: A): A = step(acc) match {
    case None => acc
    case Some(acc) => loop(acc)
  }
  loop(acc)
}
def iterateStep(e: Expr): Expr = {
  // Check e is well-typed in that it doesn't throw StaticTypeError.
  val _ = hastype(e)
  // Iterate step at full speed.
  iterate(e) {
    // ReducesToValue
    case v if isValue(v) => None
    // ReducesToStep
    case e1 => Some(step(e1))
  }
}

defined function iterate
defined function iterateStep

In [85]:
iterateStep(e_welltyped)

res85: Expr = N(n = 4.0)

# Soundness Check

In [86]:
def iterateStepPAP(e: Expr): Expr = {
  // Check initial e is well-typed in that it doesn't throw StaticTypeError.
  val ty = hastype(e)
  // Iterate step at full speed.
  iterate(e) {
    // ReducesValue
    case v if isValue(v) => None
    // ReducesProgressAndPreservation
    case e => {
      val e_ = step(e)
      val ty_ = hastype(e_)
      require(ty == ty_)
      require(e != e_)
      Some(e_)
    }
  }
}

defined function iterateStepPAP

In [76]:
val e2 = Call(Fun(("i", TNumber), Var("i")), N(2))
iterateStepPAP(e2)
iterateStep(e2)

e2: Call = Call(
  e1 = Fun(xt = ("i", TNumber), e1 = Var(x = "i")),
  e2 = N(n = 2.0)
)
res76_1: Expr = N(n = 2.0)
res76_2: Expr = N(n = 2.0)

# Add plus

In [37]:
// ((x: Number) => x + 4)(2);
// ((x: Number) => ((y: Number) => x + y))(4)(3);

In [77]:
trait Typ                                                 // τ
case object TNumber extends Typ                           // τ ::= number
case class TFun(xt: (String, Typ), tret: Typ) extends Typ // τ ::= (x: τ) => τ'

trait Expr                                               // e
case class N(n: Double) extends Expr                     // e ::= n
case class Fun(xt: (String, Typ), e1: Expr) extends Expr // e ::= (x: τ) => e1
case class Var(x: String) extends Expr                   // e ::= x
case class Call(e1: Expr, e2: Expr) extends Expr         // e ::= e1(e2)
case class BinPlus(e1: Expr, e2: Expr) extends Expr      // e ::= e1 + e2

def isValue(e: Expr): Boolean = e match {
  case N(_) | Fun(_, _) => true
  case _ => false
}
type TEnv = Map[String, Typ] // Γ


defined trait Typ
defined object TNumber
defined class TFun
defined trait Expr
defined class N
defined class Fun
defined class Var
defined class Call
defined class BinPlus
defined function isValue
defined type TEnv

In [78]:
case class StaticTypeError(tbad: Typ, esub: Expr, e: Expr) extends Exception {
  override def toString: String = s"invalid type ${tbad} for sub-expression ${esub} in ${e}"
}

def hastype(e: Expr): Typ = {
  def hastype(tenv: TEnv, e: Expr): Typ = e match {
    // TypeNumber
    case N(_) => TNumber
    // TypePlus 
    case BinPlus(e1, e2) => (hastype(tenv, e1), hastype(tenv, e2)) match {
      case (TNumber, TNumber) => TNumber
      case (tbad1, TNumber) => throw StaticTypeError(tbad1, e1, e)
      case (TNumber, tbad2) => throw StaticTypeError(tbad2, e2, e)
    }
    // TypeFunction
    case Fun((x,t), e1) => TFun((x,t), hastype(tenv + (x -> t), e1))
    // TypeVar
    case Var(x) => tenv(x)
    // TypeCall
    case Call(e1, e2) => hastype(tenv, e1) match {
      case TFun((_,t), tret) if t == hastype(tenv, e2) => tret
      case tbad => throw StaticTypeError(tbad, e1, e)
    }
  }
  hastype(Map.empty, e)
}

defined class StaticTypeError
defined function hastype

In [81]:
def subst(v: Expr, x: String, e: Expr) = {
  def subst(e: Expr): Expr = e match {
    case N(_) => e
    case BinPlus(e1, e2) => BinPlus(subst(e1), subst(e2))
    case Fun(yt @ (y, _), e1) => if (x == y) e else Fun(yt, subst(e1))
    case Var(y) => if (x == y) v else e
    case Call(e1, e2) => Call(subst(e1), subst(e2))
  }
  subst(e)
}

def step(e: Expr): Expr = {
  require(!isValue(e))
  e match {
    // DoCall
    case Call(Fun((y, _), e1), v2) => subst(v2, y, e1)
    // SearchCall2
    case Call(v1, e2) if isValue(v1) => Call(v1, step(e2))
    // SearchCall1
    case Call(e1, e2) => Call(step(e1), e2)
    // DoPlus
    case BinPlus(N(n1), N(n2)) => N(n1 + n2)
    // SearchPlus1
    case BinPlus(N(n1), e2) => BinPlus(N(n1), step(e2))
    // SearchPlus2
    case BinPlus(e1, e2) => BinPlus(step(e1), e2)
  }
}

defined function subst
defined function step

In [84]:
val e1 = BinPlus(BinPlus(N(3), N(2)), N(3))
val e2 = BinPlus(N(1), Call(Fun(("i", TNumber), Var("i")), N(4)))
val e3 = BinPlus(N(2), Fun(("i", TNumber), Var("i")))
hastype(e1)
hastype(e2)
iterateStep(e2)
iterateStepPAP(e2)
// hastype(e3)

e1: BinPlus = BinPlus(
  e1 = BinPlus(e1 = N(n = 3.0), e2 = N(n = 2.0)),
  e2 = N(n = 3.0)
)
e2: BinPlus = BinPlus(
  e1 = N(n = 1.0),
  e2 = Call(e1 = Fun(xt = ("i", TNumber), e1 = Var(x = "i")), e2 = N(n = 4.0))
)
e3: BinPlus = BinPlus(
  e1 = N(n = 2.0),
  e2 = Fun(xt = ("i", TNumber), e1 = Var(x = "i"))
)
res84_3: Typ = TNumber
res84_4: Typ = TNumber
res84_5: Expr = N(n = 5.0)
res84_6: Expr = N(n = 5.0)